# Análisis de datos interactivo

In [1]:
import pandas as pd
import numpy as np

In [2]:
!pip install plotly==5.5.0

In [3]:
df = pd.read_csv('./drive/MyDrive/DatosInvestigacion/LocalTime_2015.csv', index_col=0, parse_dates=True)

In [4]:
df.head()

DC  PAAVG1H  PAMAX1H  PAMIN1H  ...  WR1H  WS1HA  WS1HM  WS1HX
Local_Time                                            ...                           
2015-01-01 01:00:00  13.1    743.2    743.6    742.8  ...  15.0    1.0    0.0    2.9
2015-01-01 02:00:00  13.1    742.6    742.8    742.4  ...  26.0    1.8    0.0    3.0
2015-01-01 03:00:00  13.1    742.1    742.4    741.9  ...  28.0    1.9    0.5    2.9
2015-01-01 04:00:00  13.0    741.8    741.9    741.7  ...  23.0    1.5    0.4    2.7
2015-01-01 05:00:00  13.0    741.8    741.9    741.7  ...  21.0    1.4    0.4    2.6

[5 rows x 49 columns]

## Líneas de tiempo

In [5]:
import plotly.express as px

In [36]:
from sklearn.preprocessing import MinMaxScaler

In [37]:
scalerRSG = MinMaxScaler()

In [127]:
df_simple = df[['SRGLOAVG1H','TAMAX1H','TAMIN1H','WS1HX','WS1HA','RHMAX1H','RHMIN1H']]

In [128]:
dfNormal = df_simple.copy()

In [129]:
scalerRSG.fit(dfNormal)

MinMaxScaler()

Se normalizan los datos para tener un gráfico entendible.

In [130]:
values = scalerRSG.transform(dfNormal)

In [131]:
for i, column in enumerate(dfNormal.columns):
  dfNormal[column] = values[:,i]

In [132]:
dfNormal.head()

SRGLOAVG1H   TAMAX1H  ...   RHMAX1H   RHMIN1H
Local_Time                                 ...                    
2015-01-01 01:00:00         0.0  0.394958  ...  0.985714  0.925926
2015-01-01 02:00:00         0.0  0.399160  ...  0.957143  0.925926
2015-01-01 03:00:00         0.0  0.411765  ...  0.928571  0.913580
2015-01-01 04:00:00         0.0  0.420168  ...  0.942857  0.913580
2015-01-01 05:00:00         0.0  0.407563  ...  0.971429  0.925926

[5 rows x 7 columns]

In [59]:
fig = px.line(dfNormal, x=df.index, y=dfNormal.columns, title='Radiación Solar Global Promedio')
fig.update_xaxes(rangeslider_visible=True,
        rangeselector=dict(
        buttons=list([
          dict(count=1, label="1d", step="day", stepmode="backward"),
          dict(count=7, label="1w", step="day", stepmode="backward"),
          dict(count=14, label="2w", step="day", stepmode="todate"),
          dict(count=1, label="1m", step="month", stepmode="backward"),
          dict(step="all")
        ]))
)
fig.show()

## Análisis de variables por mes

Se agrega una columna extra para el mes.

In [95]:
df_simple['month'] = df.index.month_name()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [67]:
df_simple.head()

SRGLOAVG1H  TAMAX1H  TAMIN1H  ...  RHMAX1H  RHMIN1H    month
Local_Time                                         ...                           
2015-01-01 01:00:00         0.0      9.7      8.1  ...       99       94  January
2015-01-01 02:00:00         0.0      9.8      9.1  ...       97       94  January
2015-01-01 03:00:00         0.0     10.1      9.7  ...       95       93  January
2015-01-01 04:00:00         0.0     10.3      9.7  ...       96       93  January
2015-01-01 05:00:00         0.0     10.0      9.0  ...       98       94  January

[5 rows x 8 columns]

In [96]:
fig = go.Figure()

for column in df_simple.columns:
  if(column == 'month'):
    continue
  fig.add_trace(go.Box(x=df_simple['month'],y=df_simple[column],name=column))

fig.show()

Los valores de la noche se descartan para no sesgar los valores de radiación Global.

In [93]:
dfDay = df_simple.between_time('07:00:00','18:00:00')

In [ ]:
import plotly.graph_objects as go

In [90]:
fig = go.Figure()

for column in dfDay.columns:
  if(column == 'month'):
    continue
  fig.add_trace(go.Box(x=dfDay['month'],y=dfDay[column],name=column))

fig.show()

## Análisis de variables por hora

In [109]:
df_horario = dfDay.copy()

In [110]:
df_horario['time'] = dfDay.index.time.astype(str)

In [113]:
df_horario.head(24)

SRGLOAVG1H  TAMAX1H  TAMIN1H  ...  RHMAX1H  RHMIN1H      time
Local_Time                                         ...                            
2015-01-01 07:00:00        15.0     10.7      9.1  ...       97       91  07:00:00
2015-01-01 08:00:00       107.0     12.2      9.5  ...       96       89  08:00:00
2015-01-01 09:00:00       394.0     15.1     12.2  ...       89       76  09:00:00
2015-01-01 10:00:00       728.0     18.1     15.1  ...       79       57  10:00:00
2015-01-01 11:00:00       428.0     18.4     16.7  ...       66       58  11:00:00
2015-01-01 12:00:00       403.0     18.5     17.2  ...       65       55  12:00:00
2015-01-01 13:00:00       709.0     20.1     18.2  ...       61       47  13:00:00
2015-01-01 14:00:00       397.0     19.7     18.4  ...       57       49  14:00:00
2015-01-01 15:00:00       594.0     20.7     18.5  ...       58       48  15:00:00
2015-01-01 16:00:00       308.0     20.6     15.5  ...       87       50  16:00:00
2015-01-01 17:00:00       136.0     15.5     14.0  ...       95       86  17:00:00
2015-01-01 18:00:00        35.0     14.0     13.2  ...       99       95  18:00:00
2015-01-02 07:00:00        19.0     11.0      9.8  ...       92       90  07:00:00
2015-01-02 08:00:00        97.0     13.1     11.0  ...       90       80  08:00:00
2015-01-02 09:00:00       118.0     13.8     13.1  ...       82       71  09:00:00
2015-01-02 10:00:00       227.0     15.2     13.8  ...       73       64  10:00:00
2015-01-02 11:00:00       408.0     16.6     15.0  ...       66       53  11:00:00
2015-01-02 12:00:00       674.0     18.1     16.4  ...       57       50  12:00:00
2015-01-02 13:00:00       459.0     17.7     16.2  ...       61       53  13:00:00
2015-01-02 14:00:00       377.0     16.9     16.2  ...       63       57  14:00:00
2015-01-02 15:00:00       302.0     16.8     15.7  ...       64       59  15:00:00
2015-01-02 16:00:00       310.0     17.2     15.9  ...       64       58  16:00:00
2015-01-02 17:00:00       298.0     17.9     16.4  ...       62       55  17:00:00
2015-01-02 18:00:00        63.0     16.9     15.6  ...       65       59  18:00:00

[24 rows x 8 columns]

In [112]:
fig = go.Figure()

for column in dfDay.columns:
  if(column=='time'):
    continue
  # x = horario, 
  fig.add_trace(go.Box(x=dfDay['time'],y=dfDay[column],name=column))

fig.show()

## Análisis con datos normalizados

In [133]:
df_normal_month = dfNormal.copy()

In [134]:
df_normal_month['month'] = dfNormal.index.month_name()

In [136]:
df_normal_month = df_normal_month.between_time('07:00:00','18:00:00')

In [138]:
df_normal_month.head()

SRGLOAVG1H   TAMAX1H  ...   RHMIN1H    month
Local_Time                                 ...                   
2015-01-01 07:00:00    0.012325  0.436975  ...  0.888889  January
2015-01-01 08:00:00    0.087921  0.500000  ...  0.864198  January
2015-01-01 09:00:00    0.323747  0.621849  ...  0.703704  January
2015-01-01 10:00:00    0.598192  0.747899  ...  0.469136  January
2015-01-01 11:00:00    0.351684  0.760504  ...  0.481481  January

[5 rows x 8 columns]

In [137]:
fig = go.Figure()

for column in df_normal_month.columns:
  if(column == 'month'):
    continue
  fig.add_trace(go.Box(x=df_normal_month['month'],y=df_normal_month[column],name=column))

fig.show()

In [145]:
df_normal_horario = dfNormal.copy()

In [146]:
df_normal_horario['hour'] = dfNormal.index.time.astype(str)

In [148]:
df_normal_horario = df_normal_horario.between_time('07:00:00','18:00:00')
df_normal_horario.head()

SRGLOAVG1H   TAMAX1H  ...   RHMIN1H      hour
Local_Time                                 ...                    
2015-01-01 07:00:00    0.012325  0.436975  ...  0.888889  07:00:00
2015-01-01 08:00:00    0.087921  0.500000  ...  0.864198  08:00:00
2015-01-01 09:00:00    0.323747  0.621849  ...  0.703704  09:00:00
2015-01-01 10:00:00    0.598192  0.747899  ...  0.469136  10:00:00
2015-01-01 11:00:00    0.351684  0.760504  ...  0.481481  11:00:00

[5 rows x 8 columns]

In [149]:
fig = go.Figure()

for column in df_normal_horario.columns:
  if(column == 'hour'):
    continue
  fig.add_trace(go.Box(x=df_normal_horario['hour'],y=df_normal_horario[column],name=column))

fig.show()